**Легенда учебного проекта:**
Описания предполагаемого заказчика и его целей в учебном проекте нет, есть только задачи.

- Оцените корректность проведения теста. Проверьте:
    - Соответствие данных требованиям технического задания. В случае нарушения требований оцените, насколько существенно негативное влияние на результаты теста. При проверке условий технического задания и фильтрации данных, контролируйте количество уникальных пользователей, принимающих участие в тесте – это поможет детальнее изучить влияние каждого условия на аудиторию теста.
    - Время проведения теста. Убедитесь, что оно не совпадает с маркетинговыми и другими активностями.
    - Аудиторию теста. Удостоверьтесь, что нет пересечений с конкурирующим тестом и нет пользователей, участвующих в двух группах теста одновременно. Проверьте равномерность распределения пользователей по группам и правильность их формирования.

---

## Введение

### Входящий запрос
> - Оценить корректность проведения теста
> - Проанализировать результаты теста

Для оценки корректности проведения теста требуется проверить:
- Пересечение тестовой аудитории с конкурирующим тестом;
- Совпадение теста и маркетинговых событий, другие проблемы временных границ теста.

Цель проверки корректности проведения А/В тестирования позволит понять достоверность полученных результатов - действительно ли наблюдается улучшение метрик и достигнут ожидаемый эффект. В случае некорректного проведения тестирования результаты нельзя считать верными, а следовательно принятые на их основе решения могут стать также ошибочными.

### Данные 

- Название теста: recommender_system_test;
- Группы: А (контрольная), B (новая платёжная воронка);
- Дата запуска: 2020-12-07;
- Дата остановки набора новых пользователей: 2020-12-21;
- Дата остановки: 2021-01-04;
- Аудитория: 15% новых пользователей из региона EU;
- Назначение теста: тестирование изменений, связанных с внедрением улучшенной рекомендательной системы;
- Ожидаемое количество участников теста: 6000.
- Ожидаемый эффект: за 14 дней с момента регистрации в системе пользователи покажут улучшение каждой метрики не менее, чем на 10%:
    - конверсии в просмотр карточек товаров — событие product_page
    - просмотры корзины — product_cart
    - покупки — purchase.

## Предобработка данных

### Загрузка библиотек и датасета

In [7]:
import pandas as pd
import numpy as np
import math as mth
from scipy import stats

#Подгрузка Plotly Express для интерактивных графиков
import plotly.express as px
import plotly.graph_objects as go
import plotly.figure_factory as ff

Данные содержатся в 4 датасетах:
- ab_project_marketing_events.csv
- final_ab_new_users.csv
- final_ab_events.csv
- final_ab_participants.csv

`/datasets/ab_project_marketing_events.csv` — календарь маркетинговых событий на 2020 год<br>
Структура файла:
- name — название маркетингового события;
- regions — регионы, в которых будет проводиться рекламная кампания;
- start_dt — дата начала кампании;
- finish_dt — дата завершения кампании.

`/datasets/final_ab_new_users.csv` — все пользователи, зарегистрировавшиеся в интернет-магазине в период с 7 по 21 декабря 2020 года<br>
Структура файла:
- user_id — идентификатор пользователя;
- first_date — дата регистрации;
- region — регион пользователя;
- device — устройство, с которого происходила регистрация.

`/datasets/final_ab_events.csv` — все события новых пользователей в период с 7 декабря 2020 по 4 января 2021 года<br>
Структура файла:
- user_id — идентификатор пользователя;
- event_dt — дата и время события;
- event_name — тип события;
- details — дополнительные данные о событии. Например, для покупок, purchase, в этом поле хранится стоимость покупки в долларах.

`/datasets/final_ab_participants.csv` — таблица участников тестов<br>
Структура файла:
- user_id — идентификатор пользователя;
- ab_test — название теста;
- group — группа пользователя.

In [8]:
#ab_project_marketing_events - календарь маркетинговых событий на 2020
#project_marketing = pm 

ab_pm_events = pd.read_csv('/datasets/ab_project_marketing_events.csv')

ab_pm_events.sample(5)

name                   regions    start_dt  \
7   Labor day (May 1st) Ads Campaign             EU, CIS, APAC  2020-05-01   
8    International Women's Day Promo             EU, CIS, APAC  2020-03-08   
13             Chinese Moon Festival                      APAC  2020-10-01   
5          Black Friday Ads Campaign  EU, CIS, APAC, N.America  2020-11-26   
1       St. Valentine's Day Giveaway  EU, CIS, APAC, N.America  2020-02-14   

     finish_dt  
7   2020-05-03  
8   2020-03-10  
13  2020-10-07  
5   2020-12-01  
1   2020-02-16

In [9]:
#final_ab_new_users - все пользователи, зарегистрировавшиеся в интернет-магазине в период с 7 по 21 декабря 2020
#new_users = nu

final_ab_nu = pd.read_csv('/datasets/final_ab_new_users.csv')

final_ab_nu.sample(5)

user_id  first_date region   device
48766  1CB4ACD80A8806C3  2020-12-12     EU   iPhone
60335  907BA413FD17316F  2020-12-20     EU  Android
54015  B345EA7E46E3C6EF  2020-12-13     EU      Mac
10474  A0440113C7188632  2020-12-14    CIS       PC
1853   4818CFCCF7AE5B13  2020-12-07   APAC   iPhone

In [10]:
#final_ab_events - все события новых пользователей в период с 7 декабря 2020 по 4 января 2021 

final_ab_events = pd.read_csv('/datasets/final_ab_events.csv')

final_ab_events.sample(5)

user_id             event_dt    event_name  details
401994  182B68A3FBFC0D1F  2020-12-23 07:46:02         login      NaN
158929  2DD5BB35EFFF44C1  2020-12-14 02:58:29  product_page      NaN
2280    2DE47ADF672FDD61  2020-12-08 12:17:05      purchase     4.99
268668  F3973061533F966A  2020-12-10 02:40:31         login      NaN
128214  8264F6DA5AE2CACD  2020-12-07 06:31:18  product_page      NaN

In [11]:
#final_ab_participants - таблица участников тестов
#participants = members = mb

final_ab_mb = pd.read_csv('/datasets/final_ab_participants.csv')

final_ab_mb.sample(5)

user_id group                  ab_test
16763  22E23B98C142E985     B        interface_eu_test
2600   A9E0A8057A5F07D1     A  recommender_system_test
3922   4CC6ED6ECF5B43F6     B  recommender_system_test
5162   CCA75A832EBA7DA1     B  recommender_system_test
2258   D624C989E3231875     A  recommender_system_test

### Предобработка данных

Во всех датасетах колонки с датами не приведены к типу "Дата". 

#### ab_project_marketing_events

Колонки с датой приведены к типу "Дата", пропущенных значений, дубликатов и повторяемых значений не обнаружено.

In [12]:
ab_pm_events.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14 entries, 0 to 13
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   name       14 non-null     object
 1   regions    14 non-null     object
 2   start_dt   14 non-null     object
 3   finish_dt  14 non-null     object
dtypes: object(4)
memory usage: 576.0+ bytes


In [13]:
ab_pm_events['start_dt'] = pd.to_datetime(ab_pm_events['start_dt'])
ab_pm_events['finish_dt'] = pd.to_datetime(ab_pm_events['finish_dt'])

In [14]:
ab_pm_events.isna().sum()

name         0
regions      0
start_dt     0
finish_dt    0
dtype: int64

In [15]:
print('Полных дубликатов в датасете:', ab_pm_events.duplicated().sum())

Полных дубликатов в датасете: 0


In [16]:
print('Повторяемых значений в name:', ab_pm_events['name'].count() - len(ab_pm_events['name'].unique()))

Повторяемых значений в name: 0


#### final_ab_new_users

Колонка с датой приведена к типу "Дата", пропущенных значений, дубликатов и повторяемых значений не обнаружено.

In [17]:
final_ab_nu.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 61733 entries, 0 to 61732
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   user_id     61733 non-null  object
 1   first_date  61733 non-null  object
 2   region      61733 non-null  object
 3   device      61733 non-null  object
dtypes: object(4)
memory usage: 1.9+ MB


In [18]:
final_ab_nu['first_date'] = pd.to_datetime(final_ab_nu['first_date'])

In [19]:
final_ab_nu.isna().sum()

user_id       0
first_date    0
region        0
device        0
dtype: int64

In [20]:
print('Полных дубликатов в датасете:', final_ab_nu.duplicated().sum())

Полных дубликатов в датасете: 0


In [21]:
print('Повторяемых значений в user_id:', final_ab_nu['user_id'].count() - len(final_ab_nu['user_id'].unique()))

Повторяемых значений в user_id: 0


#### final_ab_events

Колонка с датой приведена к типу "Дата", дубликатов не обнаружено.

Пропущенные значения есть только в колонке details, что связано с тем, что значения в этой колонке вводились только для события purchase. Так как здесь хранится стоимость в долларах, то и заполнялись ячейки только при совершении покупки.

Уникальных значений в user_id - 58 703.

In [22]:
final_ab_events.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440317 entries, 0 to 440316
Data columns (total 4 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   user_id     440317 non-null  object 
 1   event_dt    440317 non-null  object 
 2   event_name  440317 non-null  object 
 3   details     62740 non-null   float64
dtypes: float64(1), object(3)
memory usage: 13.4+ MB


In [23]:
final_ab_events['event_dt'] = pd.to_datetime(final_ab_events['event_dt'])

In [24]:
final_ab_events.isna().sum()

user_id            0
event_dt           0
event_name         0
details       377577
dtype: int64

In [25]:
final_ab_events.groupby('event_name')['details'].count()

event_name
login               0
product_cart        0
product_page        0
purchase        62740
Name: details, dtype: int64

In [26]:
final_ab_events['details'].min()

4.99

In [27]:
print('Полных дубликатов в датасете:', final_ab_events.duplicated().sum())

Полных дубликатов в датасете: 0


In [28]:
print('Уникальных значений в user_id:', len(final_ab_events['user_id'].unique()))

Уникальных значений в user_id: 58703


#### final_ab_mb

Колонка с датой приведена к типу "Дата", пропущенных значений, дубликатов и повторяемых значений не обнаружено.

Уникальных значений в user_id - 16 666.

In [29]:
final_ab_mb.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18268 entries, 0 to 18267
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   user_id  18268 non-null  object
 1   group    18268 non-null  object
 2   ab_test  18268 non-null  object
dtypes: object(3)
memory usage: 428.3+ KB


In [30]:
final_ab_mb.isna().sum()

user_id    0
group      0
ab_test    0
dtype: int64

In [31]:
print('Полных дубликатов в датасете:', final_ab_mb.duplicated().sum())

Полных дубликатов в датасете: 0


In [32]:
print('Уникальных значений в user_id:', len(final_ab_mb['user_id'].unique()))

Уникальных значений в user_id: 16666


## Оценка корректности проведения теста

### Время проведения

Известно, что:
- Дата запуска: 2020-12-07
- Дата остановки набора новых пользователей: 2020-12-21
- Дата остановки: 2021-01-04

Первое маркетинговое событие было запущено 2020-01-25, а последняя отметка о маркетинговых событиях - 2021-01-07. Диапазон дат находится шире дат проведения тестов, а значит с ними всё в порядке.

In [33]:
print('Дата начала событий:', ab_pm_events['start_dt'].min())
print('Дата последнего события:', ab_pm_events['finish_dt'].max())

Дата начала событий: 2020-01-25 00:00:00
Дата последнего события: 2021-01-07 00:00:00


Дата старта теста совпадает с заявленной датой запуска,а вот дата остановки указана позже, чем фактическая дата последнего события теста. Дата остановки 04 января, а факт - 30 декабря.

Следовательно, или пользователи 5 дней не проявляли никакой активности, или тест был завершён рано, или в выгрузке есть ошибка.

In [34]:
print('Дата старта теста:', final_ab_events['event_dt'].min())
print('Дата последнего события теста:', final_ab_events['event_dt'].max())

Дата старта теста: 2020-12-07 00:00:33
Дата последнего события теста: 2020-12-30 23:36:33


Если смотреть на события 30 декабря, то было запущено событие CIS New Year Gift Lottery.

In [35]:
ab_pm_events.groupby('name')['start_dt'].min().sort_values()

name
Chinese New Year Promo             2020-01-25
St. Valentine's Day Giveaway       2020-02-14
International Women's Day Promo    2020-03-08
St. Patric's Day Promo             2020-03-17
Easter Promo                       2020-04-12
Labor day (May 1st) Ads Campaign   2020-05-01
Victory Day CIS (May 9th) Event    2020-05-09
Dragon Boat Festival Giveaway      2020-06-25
4th of July Promo                  2020-07-04
Chinese Moon Festival              2020-10-01
Single's Day Gift Promo            2020-11-11
Black Friday Ads Campaign          2020-11-26
Christmas&New Year Promo           2020-12-25
CIS New Year Gift Lottery          2020-12-30
Name: start_dt, dtype: datetime64[ns]

Закончилось событие CIS New Year Gift Lottery 07 января, в то время как у теста ожидаемая остановка была 4 января. Соответственно, ни ожидаемая дата, ни фактическая отметка времени о последнем событии не совпадает с датой окончания события, а значит показатели по нему неполные.

Предыдущее событие Christmas&New Year Promo проводилось на территории EU и N.America, закончилось 03 января, что входит в рамки ожидаемой остановки, но превышает фактическую дату в данных.

Для оценки влияния кампаний на выборки будет проведена проверка гипотез о нормальности распределения данных и о равности средних значений совокупности. 

#### Проверка влияния маркетинговых кампаний

Проверка через критерий Колмогорова-Смирнова используется для определения нормальности распределения выборки. P-уровень значимости выбран стандартно: 0.05

Сформулируем гипотезы:

- **Нулевая гипотеза H0** - данные нормально распределены между выборкой с событиями за весь период и выборкой с событиями до 25 декабря
- **Альтернативная гипотеза H1** - данные распределены не нормально

In [36]:
stats.ks_2samp(final_ab_events['user_id'].value_counts().tolist(), final_ab_events[final_ab_events['event_dt'] <= '2020-12-25 00:00:00']['user_id'].value_counts().tolist())

KstestResult(statistic=0.11740377375661815, pvalue=0.0, statistic_location=6, statistic_sign=-1)

Значение pvalue меньше 0.05, а значит нулевую гипотезу отвергнуть нельзя.

Проверка осуществляется через однофакторный дисперсионный анализ, который помогает сравнить значительно ли различаются средние значения двух выборок или нет.

Сформулируем гипотезы:

- **Нулевая гипотеза H0** - все средние значения совокупности равны между выборкой с событиями за весь период и выборкой с событиями до 25 декабря
- **Альтернативная гипотеза H1** - по крайней мере одно среднее значение популяции отличаетсяот остальных

In [37]:
stats.f_oneway(final_ab_events['user_id'].value_counts().tolist(), final_ab_events[final_ab_events['event_dt'] <= '2020-12-25 00:00:00']['user_id'].value_counts().tolist())

F_onewayResult(statistic=2170.336545835187, pvalue=0.0)

Значение pvalue меньше 0.05, а значит нулевую гипотезу отвергнуть нельзя.

Таким образом, недополученные данные в ходе рекламных кампаний не оказывают заметного влияния на поведение пользователей теста.

Набор новых пользователей был осуществлён в ту же дату, что и старт теста, дата остановки также соответствует заявленной -  21 декабря.

In [38]:
print('Дата начала набора:', final_ab_nu['first_date'].min())

#Объединение таблицы новых пользователей и участников теста
final_ab_nu_rst_dt = final_ab_mb.query('ab_test == "recommender_system_test"').merge(final_ab_nu)
print('Дата последнего события в наборе:', final_ab_nu_rst_dt['first_date'].max())

Дата начала набора: 2020-12-07 00:00:00
Дата последнего события в наборе: 2020-12-21 00:00:00


### Название теста и количество участников

#### Название теста

Название теста должно быть recommender_system_test.

In [39]:
final_ab_mb.groupby('ab_test').nunique()

user_id  group
ab_test                                
interface_eu_test          11567      2
recommender_system_test     6701      2

В датасете записаны группы, принимавшие участие в двух разных тестах, при этом дублирующихся значений по user_id - 1 602.

In [40]:
print('Дубликатов по user_id:', final_ab_mb['user_id'].count() - len(final_ab_mb['user_id'].unique()))

Дубликатов по user_id: 1602


Сравнение групп по тестам выявило, что все дублирующиеся пользователи находятся одновременно в обоих тестах. Также дублирующиеся пользователи находятся в двух группах - и А, и В.

In [41]:
#Проверка пересечения user_id между тестами

print('Пересечений между двумя тестами:', len(np.intersect1d(final_ab_mb.query('ab_test == "recommender_system_test"')['user_id'].unique(), final_ab_mb.query('ab_test == "interface_eu_test"')['user_id'].unique())))

Пересечений между двумя тестами: 1602


In [42]:
#ID пользователей, которые есть в обоих тестах
duplicated_users = pd.Series(np.intersect1d(final_ab_mb.query('ab_test == "recommender_system_test"')['user_id'].unique(), final_ab_mb.query('ab_test == "interface_eu_test"')['user_id'].unique()))

#Объединяем список id с их группами
duplicated = pd.concat([duplicated_users, final_ab_mb['group']], axis=1, join='inner', copy=False)

duplicated['group'].value_counts()

A    919
B    683
Name: group, dtype: int64

Так как пользователи конкурирующего теста дублируются не только в контрольной группе, но и в группе новой воронки, то правильным решением будет исключить из датасета пользователей второго теста.

In [43]:
#Разделение пользователей по группам теста
final_ab_mb_rst = final_ab_mb.query('ab_test == "recommender_system_test"')
final_ab_mb_iet = final_ab_mb.query('ab_test == "interface_eu_test"')

final_ab_mb_rst.sample(5)

user_id group                  ab_test
4627  7C09716499BF2354     B  recommender_system_test
2404  F00943852845FE90     A  recommender_system_test
6418  EE32756CFE06488B     A  recommender_system_test
4440  E021A82810DFBB5C     B  recommender_system_test
5862  49C52F2638D25D2F     A  recommender_system_test

После исключения пользователей второго теста из датасета дубликаты полностью исчезли.

In [44]:
print('Дубликатов по user_id:', final_ab_mb_rst['user_id'].count() - len(final_ab_mb_rst['user_id'].unique()))

Дубликатов по user_id: 0


#### Пересечения пользователей одного теста

Пересекающихся пользователей между группами одного теста также нет, то есть ни один пользователь на числится одновременно в группе А и группе В.

In [45]:
#Проверка пересечения user_id между группами

print('Пересечений между двумя группами:', len(np.intersect1d(final_ab_mb_rst.query('group == "A"')['user_id'].unique(), final_ab_mb_rst.query('group == "B"')['user_id'].unique())))

Пересечений между двумя группами: 0


#### Количество участников

Известно, что ожидаемое количество участников теста: 6000.

В тестовой группе находится 6 701 пользователь.

In [46]:
final_ab_mb_rst['user_id'].count()

6701

Распределение пользователей по группам не совсем равномерно: 57,1% проходил А-тест, а 42,9% - В-тест. Таким образом, в группе А оказалось на 947 пользователей больше.

In [47]:
final_ab_mb_rst.groupby('group').nunique()

user_id  ab_test
group                  
A         3824        1
B         2877        1

In [48]:
#Круговая диаграмма соотношения групп
fig = px.pie(final_ab_mb_rst, values=final_ab_mb_rst.value_counts(final_ab_mb_rst['group']).values, names=final_ab_mb_rst.value_counts(final_ab_mb_rst['group']).index, hole=0.5, title='Распределение пользователей А/В теста по группам')
fig.show("png")

ValueError: 
Image export using the "kaleido" engine requires the kaleido package,
which can be installed using pip:
    $ pip install -U kaleido


In [ ]:
print('Пользователей в группе А больше на:', final_ab_mb_rst.query('group == "A"')['user_id'].nunique() - final_ab_mb_rst.query('group == "B"')['user_id'].nunique())

Пользователей в группе А больше на: 947


### Регион

Известна информация об аудитории: 15% новых пользователей из региона EU

Так как данные о регионах есть только в датасете с пользователями теста, но отсутствуют в датасете с новыми пользователями, то добавим информацию из первого датасета во второй.

In [ ]:
final_ab_nu_rst = final_ab_mb_rst.merge(final_ab_nu)

final_ab_nu_rst.sample(5)

user_id group                  ab_test first_date region  \
3821  DE98BA6D3814A6D4     B  recommender_system_test 2020-12-10     EU   
254   6E6DC58015E1CBA0     A  recommender_system_test 2020-12-12     EU   
4837  4F26C1C82B9EA0B5     A  recommender_system_test 2020-12-14     EU   
6235  4E5468B5BBE458DE     A  recommender_system_test 2020-12-14     EU   
4355  3A73D992BFFE49A9     A  recommender_system_test 2020-12-17     EU   

       device  
3821  Android  
254        PC  
4837       PC  
6235       PC  
4355   iPhone

Основная часть новых пользователей находится в регионе EU, также как и наибольшая часть пользователей, участвующих в А/В тесте.

Доля пользователей А/В тестов относительно всех новых пользователей составляет 15%, что соответствует заявленному показателю в ТЗ.

In [ ]:
#График по регионам новых пользователей
trace1 = go.Bar(
    x = final_ab_nu['region'].value_counts().index,
    y = final_ab_nu['region'].value_counts().values,
    name = 'Новые пользователи'
)

#График по регионам пользователей теста
trace2 = go.Bar(
    x = final_ab_nu_rst['region'].value_counts().index,
    y = final_ab_nu_rst['region'].value_counts().values,
    name = 'Пользователи A/B тестов'
)

#Вывод графиков
fig = go.Figure(data=[trace1, trace2])
fig.update_layout(
    title = 'Регионы пользователей',
    barmode = 'group',
    xaxis = {'categoryorder': 'total descending'},
    yaxis_title = 'Количество пользователей',
    template='plotly_white'
)
fig.show("png")

In [ ]:
print('Количество пользователей А/В теста из EU', len(final_ab_nu_rst[final_ab_nu_rst['region'] == 'EU']) / len(final_ab_nu.query('region == "EU" & first_date <= "2020-12-21"')) * 100)

Количество пользователей А/В теста из EU 15.0


### Ожидания от метрик

Известно, что назначение теста: тестирование изменений, связанных с внедрением улучшенной рекомендательной системы. 

Ожидаемый эффект: **за 14 дней** с момента регистрации в системе пользователи покажут улучшение каждой метрики не менее, чем **на 10%**:
- конверсии в просмотр карточек товаров — событие product_page
- просмотры корзины — product_cart
- покупки — purchase

#### Лайфтайм

Так как тест был завершён раньше, чем заявлено в ТЗ, а ожидаемый эффект предполагается только по прошествии 14 дней, то некоторые пользователи А/В теста могли присоединиться к тесту позже и не получить лайфтайм в 14 дней.

Ранее уже были отфильтрованы все пользователи, совершившие события позже 25 декабря, так как в таком случае граница получается до даты последнего записанного события по факту, но не содержит неполные данные во время действия маркетинговой кампании. Теперь же отфильтруем всех пользователей, которые за 14 дней не прошли весь путь: `login -> product_page -> product_cart -> purchase`

In [ ]:
final_ab_rst_events = final_ab_nu_rst.merge(final_ab_events, how='left')
final_ab_rst_events['date_diff'] = final_ab_rst_events['event_dt'] - final_ab_rst_events['first_date']

display(final_ab_rst_events.sample(3))
print('Минимальное количество дней между регистрацией и событием:', final_ab_rst_events['date_diff'].min())
print('Максимальное количество дней между регистрацией и событием:', final_ab_rst_events['date_diff'].max())

user_id group                  ab_test first_date region  \
20896  9D1D9DC5D81268AC     B  recommender_system_test 2020-12-16     EU   
6894   A46BC3B538407EEB     A  recommender_system_test 2020-12-10     EU   
7626   9B5B1633E1F08914     A  recommender_system_test 2020-12-17     EU   

        device            event_dt    event_name  details        date_diff  
20896  Android 2020-12-17 16:42:41  product_page      NaN  1 days 16:42:41  
6894   Android                 NaT           NaN      NaN              NaT  
7626    iPhone 2020-12-28 02:37:47         login      NaN 11 days 02:37:47

Минимальное количество дней между регистрацией и событием: 0 days 00:00:04
Максимальное количество дней между регистрацией и событием: 23 days 12:42:57


В выборке есть пользователи, у которых между датой регистрации и датой события прошло больше 14 дней, поэтому отфильтруем.

In [ ]:
final_ab_rst_events['date_diff'] = final_ab_rst_events['event_dt'] - final_ab_rst_events['first_date']

print('Минимальное количество дней между регистрацией и событием:', final_ab_rst_events['date_diff'].min())
print('Максимальное количество дней между регистрацией и событием:', final_ab_rst_events['date_diff'].max())

Минимальное количество дней между регистрацией и событием: 0 days 00:00:04
Максимальное количество дней между регистрацией и событием: 23 days 12:42:57


In [ ]:
final_ab_rst_events = final_ab_rst_events.query('date_diff <= "14 days"')
final_ab_rst_events.sample(5)

user_id group                  ab_test first_date region  \
23802  41C7928F2ED27E66     A  recommender_system_test 2020-12-17     EU   
23102  33F738F2E16C7148     B  recommender_system_test 2020-12-14     EU   
16445  64E7466FBB579E9E     A  recommender_system_test 2020-12-21     EU   
2052   5EE1190E48EC36B0     A  recommender_system_test 2020-12-20     EU   
7896   F9B39A46A299971D     A  recommender_system_test 2020-12-07     EU   

        device            event_dt    event_name  details       date_diff  
23802      Mac 2020-12-22 12:07:51      purchase     4.99 5 days 12:07:51  
23102   iPhone 2020-12-18 12:29:10         login      NaN 4 days 12:29:10  
16445  Android 2020-12-21 09:11:43         login      NaN 0 days 09:11:43  
2052    iPhone 2020-12-24 11:27:08         login      NaN 4 days 11:27:08  
7896        PC 2020-12-08 06:30:14  product_cart      NaN 1 days 06:30:14

#### Пользователи с лайфтаймом 14 дней

После фильтрации всех пользователей, которые имели лайфтам меньше 14 дней, в группе остались только 3 675 человек - на 2 325 пользователей меньше предполагаемого количества.

In [ ]:
final_ab_rst_events['user_id'].nunique()

3675

Распределение пользователей после фильтрации по лайфтайму стало неравномерным: в группе А находится  74,7% пользователей, что на 1 819 человек больше, чем в группе В, где находится только 25,3% пользователей. Такая неравномерность может искажать результаты теста в пользу группы А.

In [ ]:
final_ab_rst_events.groupby('group')['user_id'].nunique()

group
A    2747
B     928
Name: user_id, dtype: int64

In [ ]:
#Круговая диаграмма соотношения групп
fig = px.pie(final_ab_rst_events, values=final_ab_rst_events.groupby('group')['user_id'].nunique().values, names=final_ab_rst_events.groupby('group')['user_id'].nunique().index, hole=0.5, title='Распределение пользователей А/В теста по группам')
fig.show("png")

In [ ]:
print('Пользователей в группе А больше на:', final_ab_rst_events.query('group == "A"')['user_id'].nunique() - final_ab_rst_events.query('group == "B"')['user_id'].nunique())

Пользователей в группе А больше на: 1819


## Исследовательский анализ данных

Так как пользователи распределены неравномерно, то для оценки событий будет в том числе применяться условие "probability" - вероятность совершения события, а не "count" - количество фактически совершённых событий. Вероятность поможет получить более точную оценку, т.к по количеству лидировать будет группа А, но именно по причине того, что в группе гораздо больше пользователей.

Также будут выведены отдельные переменные для событий: по всем пользователям, по каждой группе отдельно.

In [ ]:
#Новая переменная для событий всех пользователей А/В теста

final_ab_rst_funnel = final_ab_rst_events.pivot_table(index=['event_name'], values=['user_id'], 
                 aggfunc={'user_id': ['count', 'nunique']}).sort_values(('user_id', 'count'), ascending=False).reindex(['login', 'product_page', 'product_cart', 'purchase']).reset_index()
final_ab_rst_funnel.columns = ['event_name', 'event_sum','event_users']

#Среднее количество событий на 1 пользователя
final_ab_rst_funnel['events_mean'] = round(final_ab_rst_funnel['event_sum']/final_ab_rst_funnel['event_users'], 2)

#Доля пользователей, совершивших событие, к общему числу пользователей
final_ab_rst_funnel['total_ratio'] = round(final_ab_rst_funnel['event_users']/final_ab_rst_events['user_id'].nunique() * 100, 2)

display(final_ab_rst_funnel)

event_name  event_sum  event_users  events_mean  total_ratio
0         login      10794         3674         2.94        99.97
1  product_page       6684         2303         2.90        62.67
2  product_cart       3146         1079         2.92        29.36
3      purchase       3232         1128         2.87        30.69

In [ ]:
#Новая переменная для событий группы А
final_a_rst_events = final_ab_rst_events.query('group == "A"')

final_a_rst_funnel = final_a_rst_events.pivot_table(index=['event_name'], values=['user_id'], 
                 aggfunc={'user_id': ['count', 'nunique']}).sort_values(('user_id', 'count'), ascending=False).reindex(['login', 'product_page', 'product_cart', 'purchase']).reset_index()
final_a_rst_funnel.columns = ['event_name', 'event_sum','event_users_a']

#Среднее количество событий на 1 пользователя
final_a_rst_funnel['events_mean'] = round(final_a_rst_funnel['event_sum']/final_a_rst_funnel['event_users_a'], 2)

#Доля пользователей, совершивших событие, к общему числу пользователей
final_a_rst_funnel['total_ratio'] = round(final_a_rst_funnel['event_users_a']/final_ab_rst_events['user_id'].nunique() * 100, 2)

display(final_a_rst_funnel)

event_name  event_sum  event_users_a  events_mean  total_ratio
0         login       8337           2747         3.03        74.75
1  product_page       5371           1780         3.02        48.44
2  product_cart       2495            824         3.03        22.42
3      purchase       2598            872         2.98        23.73

In [ ]:
#Новая переменная для событий группы В
final_b_rst_events = final_ab_rst_events.query('group == "B"')

final_b_rst_funnel = final_b_rst_events.pivot_table(index=['event_name'], values=['user_id'], 
                 aggfunc={'user_id': ['count', 'nunique']}).sort_values(('user_id', 'count'), ascending=False).reindex(['login', 'product_page', 'product_cart', 'purchase']).reset_index()
final_b_rst_funnel.columns = ['event_name', 'event_sum','event_users_b']

#Среднее количество событий на 1 пользователя
final_b_rst_funnel['events_mean'] = round(final_b_rst_funnel['event_sum']/final_b_rst_funnel['event_users_b'], 2)

#Доля пользователей, совершивших событие, к общему числу пользователей
final_b_rst_funnel['total_ratio'] = round(final_b_rst_funnel['event_users_b']/final_ab_rst_events['user_id'].nunique() * 100, 2)

display(final_b_rst_funnel)

event_name  event_sum  event_users_b  events_mean  total_ratio
0         login       2457            927         2.65        25.22
1  product_page       1313            523         2.51        14.23
2  product_cart        651            255         2.55         6.94
3      purchase        634            256         2.48         6.97

### Количество событий на пользователя

По среднему количеству действий на пользователя ожидаемо лидирует событие `login`, которое является первым. Однако, в целом разница не сильно заметна - все пользователи как суммарно, так и внутри групп совершали в среднем 2-3 действия на каждом из событий.

In [ ]:
display('Событий на всех пользователей А/В', final_ab_rst_funnel[['event_name', 'events_mean']])
display('Событий на пользователей группы А', final_a_rst_funnel[['event_name', 'events_mean']])
display('Событий на пользователей группы В', final_b_rst_funnel[['event_name', 'events_mean']])

'Событий на всех пользователей А/В'

event_name  events_mean
0         login         2.94
1  product_page         2.90
2  product_cart         2.92
3      purchase         2.87

'Событий на пользователей группы А'

event_name  events_mean
0         login         3.03
1  product_page         3.02
2  product_cart         3.03
3      purchase         2.98

'Событий на пользователей группы В'

event_name  events_mean
0         login         2.65
1  product_page         2.51
2  product_cart         2.55
3      purchase         2.48

Так как группы были распределены неравномерно, посмотрим также вероятность совершения события.

На графике видно, что доля пользователей к количеству совершённых действий была выше у группы В, что подтверждается долей пользователей к количеству совершённых действий. 40,43% пользователей группы В совершили действие `login`, в то время как у группы А доля равна 37,68%.

По остальным событиям доля пользователей к количеству совершённых действий выше у группы В, но доля пользователей, совершивших событие, к общему числу пользователей значительно выше у группы А. Поэтому вероятность совершения события на остальных этапах всё же немного выше именно у группы А.

In [ ]:
#График вероятности событий по группам
fig = px.histogram(final_ab_rst_events, x='event_name', y='user_id', color='group', histfunc='count', histnorm='probability', barmode ='group', title='События').update_layout(xaxis_title="События воронки", yaxis_title="Вероятность").update_xaxes(categoryorder="total descending")
fig.show("png")

### Распределение по дням

Пользователи групп А и В показывают разное поведение:
- Группа А была слабо активна в первые недели теста, но стала активно совершать действия ближе к его завершению
- Группа В активность проявляла стабильно каждую неделю, но при этом проявляла спад в выходные дни

In [ ]:
fig = px.histogram(final_ab_rst_events, x='event_dt', y='user_id', color='group', histfunc='count', histnorm='probability', barmode ='overlay', nbins=27, title='События').update_layout(xaxis_title="Даты событий", yaxis_title="Вероятность").update_xaxes(categoryorder="total descending")
fig.show("png")

Набор пользователей был выше 07, 14 и 21 декабря.

In [ ]:
#Количество набранных пользователей группы А по датам
#final_ab_nu_rst[final_ab_nu_rst['group'] == 'A']['first_date'].value_counts()

In [ ]:
fig = px.histogram(final_ab_nu_rst.query('group == "A"'), x='first_date', y='user_id', histfunc='count', title='Набор пользователей').update_layout(xaxis_title="Дни набора", yaxis_title="Количество").update_xaxes(categoryorder="total descending")
fig.show("png")

Несмотря на то, что 14 декабря пользователей набирали не значительно больше, чем в предыдущие дни, количество действий, совершённых группой А оказалось довольно много. 2 756 действий 14 декабря, что на 721 действие больше, чем количество действий второго по активности дня - 21 декабря.

In [ ]:
#final_ab_rst_events[final_ab_rst_events['group'] == 'A']['first_date'].value_counts()

In [ ]:
fig = px.histogram(final_ab_rst_events.query('group == "A" and event_name == "login"'), x='event_dt', y='user_id', histfunc='count', nbins=27, title='Количество пользователей группы А по событию login').update_layout(xaxis_title="Даты событий", yaxis_title="Количество пользователей").update_xaxes(categoryorder="total descending")
fig.show("png")

Наиболее активно пользователи регистрировались с 14 по 21 декабря. То есть по какой-то причине пользователи предпочли пройти регистрацию именно в этот день.

### Конверсия по воронкам

Ожидаемый эффект был - 10% улучшения по каждому этапу.

In [ ]:
final_ab_rst_funnel['users_step_ratio'] = round(final_ab_rst_funnel['event_users']/final_ab_rst_funnel['event_users'].shift(1) * 100, 2)
final_a_rst_funnel['users_step_ratio'] = round(final_a_rst_funnel['event_users_a']/final_a_rst_funnel['event_users_a'].shift(1) * 100, 2)
final_b_rst_funnel['users_step_ratio'] = round(final_b_rst_funnel['event_users_b']/final_b_rst_funnel['event_users_b'].shift(1) * 100, 2)

#### По всем участникам

До конца дошло примерно 30% всех участников теста.

От `login` к `product_page` дошло примерно 63% пользователей, от `product_page` к `purchase`примерно 49%, а от `purchase` к `product_cart` примерно 96%. Таким образом, наибольшие потери происходят на первых трёх шагах, при этом потери значительные.

Также стоит отметить, что некоторые пользователи переходят к покупке напрямую, минуя этап с корзиной.

In [ ]:
display('Конверсия у всех пользователей А/В', final_ab_rst_funnel[['event_name', 'users_step_ratio', 'total_ratio']])

'Конверсия у всех пользователей А/В'

event_name  users_step_ratio  total_ratio
0         login               NaN        99.97
1  product_page             62.68        62.67
2  product_cart             46.85        29.36
3      purchase            104.54        30.69

In [ ]:
#Воронка событий по всем пользователям
fig = px.funnel(final_ab_rst_funnel, x=final_ab_rst_funnel['event_users'], y=final_ab_rst_funnel['event_name'], title='Воронка событий по всем пользователям А/В теста')
fig.update_traces(showlegend=False)
fig.show("png")

#### По группам

В разрезе групп чаще до конца доходили пользователи В, чем пользователи А. 18,25% потерь в группе В против 52,33% потерь в группе А. Однако, такой разрыв может быть снова связан с неравномерным распределением.


In [ ]:
display('Конверсия у пользователей группы А', final_a_rst_funnel[['event_name', 'users_step_ratio', 'total_ratio']])
display('Конверсия у пользователей группы В', final_b_rst_funnel[['event_name', 'users_step_ratio', 'total_ratio']])

'Конверсия у пользователей группы А'

event_name  users_step_ratio  total_ratio
0         login               NaN        74.75
1  product_page             64.80        48.44
2  product_cart             46.29        22.42
3      purchase            105.83        23.73

'Конверсия у пользователей группы В'

event_name  users_step_ratio  total_ratio
0         login               NaN        25.22
1  product_page             56.42        14.23
2  product_cart             48.76         6.94
3      purchase            100.39         6.97

Что касается достижения ожидаемого эффекта, то он не был достигнут:

- На 9% уменьшилась конверсия на событии просмотра страницы продукта
- На 3% выросла конверсия по событию с корзиной
- На 6% уменьшилась конверсия по событию с покупкой

Результаты нельзя считать достоверными по всем событиям, т.к. пользователи проходили воронку не по всем этапам.

In [ ]:
fig = go.Figure()

fig.add_trace(go.Funnel(
    name = 'A',
    y = final_a_rst_funnel['event_name'],
    x = final_a_rst_funnel['event_users_a'],
    textinfo = "value+percent previous"))

fig.add_trace(go.Funnel(
    name = 'B',
    y = final_b_rst_funnel['event_name'],
    x = final_b_rst_funnel['event_users_b'],
    textinfo = "value+percent previous"))

fig.update_layout(title = {'text' : 'Воронка событий пользователей в разрезе групп А и В'})
fig.show("png")

### Особенности A/B тестирования

Основными ошибками при проведении А/В тестирования являются:
- Некорректное деление трафика теста
 - Неравномерное распределение между сегментами по количеству или выборка групп с разными признаками искажает результаты теста
- Слишком маленькая или слишком большая выборка
- Слишком быстрый или слишком долгий срок тестирования
- Проблема подглядывания
 - Наблюдается в случае, когда результаты анализируют до окончания теста

## Оценка А/В тестирования

### Общая оценка

Результаты А/В тестирования нельзя считать достоверными, т.к:
- Выборки распределены неравномерно, в группе А было 74,7% пользователей, а в группе В только 25,3%
- Тест был завершён слишком рано, дата последнего зафиксированного события не соответствует заявленной в ТЗ дате остановке теста
- В ТЗ была чёткая установка о количестве пользователей из EU, однако, несмотря на то, что процент соответствует, в выборке есть пользователи и из других регионов

### Статистическая разница долей

Величина Z — стандартная для критерия со стандартным нормальным распределением: со средним, равным нулю, и стандартным отклонением, равным единице.

Сформулируем гипотезы:

- **Нулевая гипотеза H0** - различия между экспериментальными группами, совершившими указанное событие, статистически не значимы
- **Альтернативная гипотеза H1** - различия между экспериментальными группами, совершившими указанное событие, статистически значимы

In [ ]:
group = final_ab_rst_events.pivot_table(index = 'event_name', columns = 'group', values = 'user_id', aggfunc = 'nunique').reset_index()
group.columns = ['event_name', 'A', 'B']
group['total'] = group['A'] + group['B']

group

event_name     A    B  total
0         login  2747  927   3674
1  product_cart   824  255   1079
2  product_page  1780  523   2303
3      purchase   872  256   1128

In [ ]:
def z_test(group_1, group_2, eventname, alpha):
    for i in group.index:
        purchases1 = group.loc[eventname, group_1]
        purchases2 = group.loc[eventname, group_2]
        n1 = group.iloc[0, 1]
        n2 = group.iloc[0, 2]
        
        # пропорция успехов в первой группе:
        p1 = purchases1 / n1
        # пропорция успехов во второй группе:
        p2 = purchases2 / n2     
        
        # пропорция успехов в комбинированном датасете:
        p_combined = p_combined = (purchases1 + purchases2) / (n1 + n2) 
        # разница пропорций в датасетах
        difference = p1 - p2
        # считаем статистику в ст.отклонениях стандартного нормального распределения
        z_value = difference / mth.sqrt(p_combined * (1 - p_combined) * (1 / n1 + 1 / n2))
        # задаем стандартное нормальное распределение (среднее 0, ст.отклонение 1)
        distr = stats.norm(0, 1) 
        p_value = (1 - distr.cdf(abs(z_value))) * 2
        
        # применим поправку Бенферрони
        bonferroni_alpha = alpha / 3
        
    print('Проверка события:', eventname)
    print('p-value: ',p_value)      

    if (p_value < bonferroni_alpha):
        print("Отвергаем нулевую гипотезу: между конверсией групп есть значимая разница")
    else:
        print("Не получилось отвергнуть нулевую гипотезу, нет оснований считать конверсию групп разной") 
    print('')

In [ ]:
for eventname in group.index[1:4]:    
    z_test('A', 'B', eventname, 0.05)

Проверка события: 1
p-value:  0.15034216422194624
Не получилось отвергнуть нулевую гипотезу, нет оснований считать конверсию групп разной

Проверка события: 2
p-value:  5.084368080776613e-06
Отвергаем нулевую гипотезу: между конверсией групп есть значимая разница

Проверка события: 3
p-value:  0.018474632659979617
Не получилось отвергнуть нулевую гипотезу, нет оснований считать конверсию групп разной



Разница значима для события `product_page`, для остальных событий разница не статистически значима.

## Заключение

А/В тестирование было проведено с ошибками, а потому полученные результаты нельзя считать достоверными. Есть ошибки как по выборкам, так и по датам проведения, а также одновременно с целевым тестом проводился и конкурирующий, из-за чего часть пользователей попала в группы обеих тестов.

Что касается пересечения с рекламными кампаниями, то тест пересёкся с событием Christmas&New Year Promo, но при этом был закончен раньше окончания события. Данные получаются неполными, но при их удалении теряется информация за 5 дней.

А/В тестирование необходимо провести повторно, учитывая следующие моменты:
- Проводиться должен только 1 тест
- Выборки должны соответствововать цели: если интересует регион EU, то не добавлять пользователей из других регионов. Если ожидается 6 000 участников, то убедиться, что все из них соответствуют параметрам. В данном же случае не все участники были из EU и не все из них набрали лайфтайм в 14 дней
- Выборки должны быть равномерными, идеально соотношение 50 на 50
- Тестирование должно проводиться по воронке событий. По факту же пользователи могли пропускать этап с корзиной, из-за чего оценка конверсии может быть неточной
- Учитывать влияние рекламных кампаний, возможно, что некоторые события могут изменить поведение пользователей. В данном случае тест пересёкся с событием Christmas&New Year Promo, но при этом был закончен раньше окончания события, однако  закончились позже фактической остановки теста, но заметного влияния на поведение пользователей не оказали

---


**Оценка от ревьюера Яндекс.Практикума**
    
`````
Общий вывод по проекту:
У тебя получилась очень сильная и хорошая работа. Здорово, что расчеты ты сопровождаешь иллюстрациями, а так же не забываешь про комментарии, твой проект интересно проверять. 
Твой проект так и просится на github =)   

`````